In [5]:
#import wradlib as wrl
import os
import numpy as np
import matplotlib as mpl
import matplotlib.pyplot as pl
import warnings
warnings.filterwarnings('ignore')
try:
    get_ipython().magic("matplotlib inline")
except:
    pl.ion()
from scipy import interpolate
import datetime as dt
import glob
import json
from datetime import datetime
from datetime import timedelta

import pandas as pd

import metpy.calc as mpcalc
from metpy.cbook import get_test_data
from metpy.plots import add_metpy_logo, Hodograph, SkewT
from metpy.units import units

import numpy as np
import xarray as xr
#from netCDF4 import Dataset
from rpy2.robjects.packages import importr
from rpy2.robjects import r,pandas2ri
import rpy2.robjects as robjects
import rpy2.robjects.numpy2ri
rpy2.robjects.numpy2ri.activate()
pandas2ri.activate()
#importr('thunder')
base = importr('base')
print(base._libPaths())
importr('thunder')

[1] "/home/lmathias/anaconda3/envs/metpy/lib/R/library"



rpy2.robjects.packages.Package as a <module 'thunder'>

In [6]:
os.chdir('/data/ecmwf')
data = xr.open_dataset('ec_pl.nc')
data_sfc = xr.open_dataset('ec_sfc.nc')

# View a summary of the Dataset
print(data)

<xarray.Dataset>
Dimensions:    (time: 48, longitude: 61, latitude: 31, level: 15)
Coordinates:
  * time       (time) datetime64[ns] 2023-02-03T01:00:00 ... 2023-02-05
  * longitude  (longitude) float32 3.0 3.1 3.2 3.3 3.4 ... 8.6 8.7 8.8 8.9 9.0
  * latitude   (latitude) float32 51.0 50.9 50.8 50.7 ... 48.3 48.2 48.1 48.0
  * level      (level) float64 100.0 150.0 200.0 250.0 ... 925.0 950.0 1e+03
Data variables:
    t          (time, level, latitude, longitude) float32 ...
    q          (time, level, latitude, longitude) float32 ...
    z          (time, level, latitude, longitude) float32 ...
    u          (time, level, latitude, longitude) float32 ...
    v          (time, level, latitude, longitude) float32 ...
Attributes:
    CDI:          Climate Data Interface version ?? (http://mpimet.mpg.de/cdi)
    Conventions:  CF-1.6
    history:      Fri Feb 03 06:50:03 2023: cdo merge temp.nc qhum.nc geopot....
    CDO:          Climate Data Operators version 1.9.3 (http://mpimet.mpg.d

In [3]:
for i in range(48):

    data = data.metpy.parse_cf()
    data_sfc = data_sfc.metpy.parse_cf()

    time = data['z'].metpy.time

    timeinit = time[0]
    timeinit = datetime.utcfromtimestamp(timeinit.item()/1e9)-timedelta(hours=1)
    print(timeinit)
    
    

    temp = data['t']
    qhum = data['q']
    uwind = data['u']
    vwind = data['v']
    geopot = data['z']
    press = data['level']

    sfctemp = data_sfc['t2m']
    sfcdew = data_sfc['d2m']
    pwat = data_sfc['tcwv']
    deg0l = data_sfc['deg0l']
    sfcpress =  data_sfc['sp']
    sfcuwind =  data_sfc['u10']
    sfcvwind =  data_sfc['v10']
    sfcgeopot =  data_sfc['z']

    ##############################################################

    lat = 49.6
    lon = 6.1

    #i = 0 # set time step

    temp = temp.metpy.loc[{'time': time[i], 'latitude': lat, 'longitude': lon}]
    sfctemp = sfctemp.metpy.loc[{'time': time[i], 'latitude': lat, 'longitude': lon}]
    sfcdew = sfcdew.metpy.loc[{'time': time[i], 'latitude': lat, 'longitude': lon}]
    sfcpress = sfcpress.metpy.loc[{'time': time[i], 'latitude': lat, 'longitude': lon}]
    sfcuwind = sfcuwind.metpy.loc[{'time': time[i], 'latitude': lat, 'longitude': lon}]
    sfcvwind = sfcvwind.metpy.loc[{'time': time[i], 'latitude': lat, 'longitude': lon}]
    sfcgeopot = sfcgeopot.metpy.loc[{'time': time[i], 'latitude': lat, 'longitude': lon}]
    qhum = qhum.metpy.loc[{'time': time[i], 'latitude': lat, 'longitude': lon}]
    geopot = geopot.metpy.loc[{'time': time[i], 'latitude': lat, 'longitude': lon}]
    uwind = uwind.metpy.loc[{'time': time[i], 'latitude': lat, 'longitude': lon}]
    vwind = vwind.metpy.loc[{'time': time[i], 'latitude': lat, 'longitude': lon}]
    pwat = pwat.metpy.loc[{'time': time[i], 'latitude': lat, 'longitude': lon}]
    deg0l = deg0l.metpy.loc[{'time': time[i], 'latitude': lat, 'longitude': lon}]

    temp[14] = sfctemp
    uwind[14] = sfcuwind
    vwind[14] = sfcvwind
    geopot[14] = sfcgeopot
    press = np.where(press==1000, sfcpress/100, press)
    
    #sfcpress.data=92000
    
    if sfcpress.item(0) <= 95200:
                temp = np.delete(temp,13)
                qhum = np.delete(qhum,13)
                geopot = np.delete(geopot,13)
                uwind = np.delete(uwind,13)
                vwind = np.delete(vwind,13)
                press = np.delete(press,13)
                
    if sfcpress.item(0) <= 92700:
                temp = np.delete(temp,12)
                qhum = np.delete(qhum,12)
                geopot = np.delete(geopot,12)
                uwind = np.delete(uwind,12)
                vwind = np.delete(vwind,12)
                press = np.delete(press,12)
    
    k = np.size(press)-3
    
    
    press = press[::-1]
    qhum = qhum.data[::-1]*units('kg/kg')
    uwind = uwind.data[::-1]
    vwind = vwind.data[::-1]
    geopot = geopot.data[::-1]*units('meters**2/second**2')
    temp = temp-273.15
    temp = temp.data[::-1]*units.degC

    dew = mpcalc.dewpoint_from_specific_humidity(press*units.hPa, temp, qhum)
    sfcdew = sfcdew.data.item()-273.15
    dew[0] = sfcdew*units.degC
    pwat = pwat.data.item()
    pwat = pwat*units.mm
    deg0l = deg0l.data.item()
    deg0l = deg0l*units.meters
    height = mpcalc.geopotential_to_height(geopot)


    # compute convective parameters
    ws = np.sqrt(uwind**2 + vwind**2)*1.94384
    ws = list(ws)
    pressure = list(press)
    temp2 = list(temp.magnitude)
    altitude = list(height.magnitude)
    dpt= list(dew.magnitude)
    wd = mpcalc.wind_direction(uwind* units('meters/second'), vwind* units('meters/second'), convention='from')
    wd = list(wd.magnitude)
    ws = robjects.IntVector(ws)
    wd = robjects.IntVector(wd)
    dpt = robjects.IntVector(dpt)
    altitude = robjects.IntVector(altitude)
    pressure = robjects.IntVector(pressure)
    temp2 = robjects.IntVector(temp2)
    print(altitude)
    time2 = str(i+1)
    robjects.r['sounding_save'](pressure,altitude,temp2,dpt,wd,ws, max_speed=30, filename='ecmwf_sounding_luxcity_%s.png' %time2,title='ECMWF | Luxembourg | '+ timeinit.strftime('Init: %d.%m.%Y %H:%M UTC')
              + time[i].dt.strftime(' | Valid: %d.%m.%Y %H:%M UTC').item())

Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitud

2023-02-03 00:00:00
 [1]   313   667   883  1104  1563  2045  3109  4307  5673  7274  9219 10381
[13] 11735 13451 15932



Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitud

2023-02-03 00:00:00
 [1]   313   660   876  1097  1555  2043  3110  4310  5679  7280  9224 10384
[13] 11735 13445 15933



Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitud

...

2023-02-03 00:00:00
 [1]   313   731   947  1167  1625  2106  3159  4357  5732  7337  9285 10455
[13] 11826 13571 16073



Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitud

2023-02-03 00:00:00
 [1]   313   730   946  1167  1625  2105  3158  4356  5730  7334  9283 10454
[13] 11826 13573 16076



Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitud

2023-02-03 00:00:00
 [1]   313   731   947  1167  1625  2106  3157  4354  5728  7331  9279 10452
[13] 11823 13571 16078



In [4]:
for i in range(48):

    data = data.metpy.parse_cf()
    data_sfc = data_sfc.metpy.parse_cf()

    time = data['z'].metpy.time

    timeinit = time[0]
    timeinit = datetime.utcfromtimestamp(timeinit.item()/1e9)-timedelta(hours=1)
    print(timeinit)

    temp = data['t']
    qhum = data['q']
    uwind = data['u']
    vwind = data['v']
    geopot = data['z']
    press = data['level']

    sfctemp = data_sfc['t2m']
    sfcdew = data_sfc['d2m']
    pwat = data_sfc['tcwv']
    deg0l = data_sfc['deg0l']
    sfcpress =  data_sfc['sp']
    sfcuwind =  data_sfc['u10']
    sfcvwind =  data_sfc['v10']
    sfcgeopot =  data_sfc['z']

    ##############################################################

    lat = 50.1
    lon = 6.0

    #i = 0 # set time step

    temp = temp.metpy.loc[{'time': time[i], 'latitude': lat, 'longitude': lon}]
    sfctemp = sfctemp.metpy.loc[{'time': time[i], 'latitude': lat, 'longitude': lon}]
    sfcdew = sfcdew.metpy.loc[{'time': time[i], 'latitude': lat, 'longitude': lon}]
    sfcpress = sfcpress.metpy.loc[{'time': time[i], 'latitude': lat, 'longitude': lon}]
    sfcuwind = sfcuwind.metpy.loc[{'time': time[i], 'latitude': lat, 'longitude': lon}]
    sfcvwind = sfcvwind.metpy.loc[{'time': time[i], 'latitude': lat, 'longitude': lon}]
    sfcgeopot = sfcgeopot.metpy.loc[{'time': time[i], 'latitude': lat, 'longitude': lon}]
    qhum = qhum.metpy.loc[{'time': time[i], 'latitude': lat, 'longitude': lon}]
    geopot = geopot.metpy.loc[{'time': time[i], 'latitude': lat, 'longitude': lon}]
    uwind = uwind.metpy.loc[{'time': time[i], 'latitude': lat, 'longitude': lon}]
    vwind = vwind.metpy.loc[{'time': time[i], 'latitude': lat, 'longitude': lon}]
    pwat = pwat.metpy.loc[{'time': time[i], 'latitude': lat, 'longitude': lon}]
    deg0l = deg0l.metpy.loc[{'time': time[i], 'latitude': lat, 'longitude': lon}]

    temp[14] = sfctemp
    uwind[14] = sfcuwind
    vwind[14] = sfcvwind
    geopot[14] = sfcgeopot
    press = np.where(press==1000, sfcpress/100, press)
    
    
    if sfcpress.item(0) <= 95200:
                temp = np.delete(temp,13)
                qhum = np.delete(qhum,13)
                geopot = np.delete(geopot,13)
                uwind = np.delete(uwind,13)
                vwind = np.delete(vwind,13)
                press = np.delete(press,13)
                
    if sfcpress.item(0) <= 92700:
                temp = np.delete(temp,12)
                qhum = np.delete(qhum,12)
                geopot = np.delete(geopot,12)
                uwind = np.delete(uwind,12)
                vwind = np.delete(vwind,12)
                press = np.delete(press,12)
    
    k = np.size(press)-3
    
    
    press = press[::-1]
    qhum = qhum.data[::-1]*units('kg/kg')
    uwind = uwind.data[::-1]
    vwind = vwind.data[::-1]
    geopot = geopot.data[::-1]*units('meters**2/second**2')
    temp = temp-273.15
    temp = temp.data[::-1]*units.degC

    dew = mpcalc.dewpoint_from_specific_humidity(press*units.hPa, temp, qhum)
    sfcdew = sfcdew.data.item()-273.15
    dew[0] = sfcdew*units.degC
    pwat = pwat.data.item()
    pwat = pwat*units.mm
    deg0l = deg0l.data.item()
    deg0l = deg0l*units.meters
    height = mpcalc.geopotential_to_height(geopot)


    # compute convective parameters
    ws = np.sqrt(uwind**2 + vwind**2)*1.94384
    ws = list(ws)
    pressure = list(press)
    temp2 = list(temp.magnitude)
    altitude = list(height.magnitude)
    dpt= list(dew.magnitude)
    wd = mpcalc.wind_direction(uwind* units('meters/second'), vwind* units('meters/second'), convention='from')
    wd = list(wd.magnitude)
    ws = robjects.IntVector(ws)
    wd = robjects.IntVector(wd)
    dpt = robjects.IntVector(dpt)
    altitude = robjects.IntVector(altitude)
    pressure = robjects.IntVector(pressure)
    temp2 = robjects.IntVector(temp2)
    print(altitude)
    time2 = str(i+1)
    robjects.r['sounding_save'](pressure,altitude,temp2,dpt,wd,ws, max_speed=30, filename='ecmwf_sounding_tvierges_%s.png' %time2,title='ECMWF | Troisvierges | '+ timeinit.strftime('Init: %d.%m.%Y %H:%M UTC')
              + time[i].dt.strftime(' | Valid: %d.%m.%Y %H:%M UTC').item())

Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitud

2023-02-03 00:00:00
 [1]   474   655   871  1093  1551  2034  3098  4298  5668  7271  9217 10379
[13] 11732 13437 15923



Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitud

2023-02-03 00:00:00
 [1]   474   651   867  1088  1547  2031  3097  4299  5673  7277  9222 10380
[13] 11729 13440 15920



Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitud

...

2023-02-03 00:00:00
 [1]   474   730   946  1167  1625  2106  3159  4357  5731  7334  9282 10452
[13] 11823 13564 16069



Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitud

2023-02-03 00:00:00
 [1]   474   730   946  1167  1625  2106  3158  4355  5729  7331  9279 10450
[13] 11821 13565 16074



Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitud

2023-02-03 00:00:00
 [1]   474   731   946  1167  1625  2106  3157  4354  5726  7329  9275 10447
[13] 11818 13565 16074



In [6]:
for i in range(48):

    data = data.metpy.parse_cf()
    data_sfc = data_sfc.metpy.parse_cf()

    time = data['z'].metpy.time

    timeinit = time[0]
    timeinit = datetime.utcfromtimestamp(timeinit.item()/1e9)-timedelta(hours=1)
    print(timeinit)

    temp = data['t']
    qhum = data['q']
    uwind = data['u']
    vwind = data['v']
    geopot = data['z']
    press = data['level']

    sfctemp = data_sfc['t2m']
    sfcdew = data_sfc['d2m']
    pwat = data_sfc['tcwv']
    deg0l = data_sfc['deg0l']
    sfcpress =  data_sfc['sp']
    sfcuwind =  data_sfc['u10']
    sfcvwind =  data_sfc['v10']
    sfcgeopot =  data_sfc['z']

    ##############################################################

    lat = 49.3
    lon = 6.2

    #i = 0 # set time step

    temp = temp.metpy.loc[{'time': time[i], 'latitude': lat, 'longitude': lon}]
    sfctemp = sfctemp.metpy.loc[{'time': time[i], 'latitude': lat, 'longitude': lon}]
    sfcdew = sfcdew.metpy.loc[{'time': time[i], 'latitude': lat, 'longitude': lon}]
    sfcpress = sfcpress.metpy.loc[{'time': time[i], 'latitude': lat, 'longitude': lon}]
    sfcuwind = sfcuwind.metpy.loc[{'time': time[i], 'latitude': lat, 'longitude': lon}]
    sfcvwind = sfcvwind.metpy.loc[{'time': time[i], 'latitude': lat, 'longitude': lon}]
    sfcgeopot = sfcgeopot.metpy.loc[{'time': time[i], 'latitude': lat, 'longitude': lon}]
    qhum = qhum.metpy.loc[{'time': time[i], 'latitude': lat, 'longitude': lon}]
    geopot = geopot.metpy.loc[{'time': time[i], 'latitude': lat, 'longitude': lon}]
    uwind = uwind.metpy.loc[{'time': time[i], 'latitude': lat, 'longitude': lon}]
    vwind = vwind.metpy.loc[{'time': time[i], 'latitude': lat, 'longitude': lon}]
    pwat = pwat.metpy.loc[{'time': time[i], 'latitude': lat, 'longitude': lon}]
    deg0l = deg0l.metpy.loc[{'time': time[i], 'latitude': lat, 'longitude': lon}]

    temp[14] = sfctemp
    uwind[14] = sfcuwind
    vwind[14] = sfcvwind
    geopot[14] = sfcgeopot
    press = np.where(press==1000, sfcpress/100, press)
    
    #sfcpress.data=92000
    
    if sfcpress.item(0) <= 95200:
                temp = np.delete(temp,13)
                qhum = np.delete(qhum,13)
                geopot = np.delete(geopot,13)
                uwind = np.delete(uwind,13)
                vwind = np.delete(vwind,13)
                press = np.delete(press,13)
                
    if sfcpress.item(0) <= 92700:
                temp = np.delete(temp,12)
                qhum = np.delete(qhum,12)
                geopot = np.delete(geopot,12)
                uwind = np.delete(uwind,12)
                vwind = np.delete(vwind,12)
                press = np.delete(press,12)
    
    k = np.size(press)-3
    
    
    press = press[::-1]
    qhum = qhum.data[::-1]*units('kg/kg')
    uwind = uwind.data[::-1]
    vwind = vwind.data[::-1]
    geopot = geopot.data[::-1]*units('meters**2/second**2')
    temp = temp-273.15
    temp = temp.data[::-1]*units.degC

    dew = mpcalc.dewpoint_from_specific_humidity(press*units.hPa, temp, qhum)
    sfcdew = sfcdew.data.item()-273.15
    dew[0] = sfcdew*units.degC
    pwat = pwat.data.item()
    pwat = pwat*units.mm
    deg0l = deg0l.data.item()
    deg0l = deg0l*units.meters
    height = mpcalc.geopotential_to_height(geopot)


    # compute convective parameters
    ws = np.sqrt(uwind**2 + vwind**2)*1.94384
    ws = list(ws)
    pressure = list(press)
    temp2 = list(temp.magnitude)
    altitude = list(height.magnitude)
    dpt= list(dew.magnitude)
    wd = mpcalc.wind_direction(uwind* units('meters/second'), vwind* units('meters/second'), convention='from')
    wd = list(wd.magnitude)
    ws = robjects.IntVector(ws)
    wd = robjects.IntVector(wd)
    dpt = robjects.IntVector(dpt)
    altitude = robjects.IntVector(altitude)
    pressure = robjects.IntVector(pressure)
    temp2 = robjects.IntVector(temp2)
    print(altitude)
    time2 = str(i+1)
    robjects.r['sounding_save'](pressure,altitude,temp2,dpt,wd,ws, max_speed=30, filename='ecmwf_sounding_tville_%s.png' %time2,title='ECMWF | Thionville | '+ timeinit.strftime('Init: %d.%m.%Y %H:%M UTC')
              + time[i].dt.strftime(' | Valid: %d.%m.%Y %H:%M UTC').item())

Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitud

2021-05-18 00:00:00
 [1]   206   540   759   983  1446  1932  2982  4161  5506  7082  9017 10228
[13] 11725 13646 16317



Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitud

2021-05-18 00:00:00
 [1]   206   544   763   986  1448  1933  2981  4157  5497  7069  9008 10224
[13] 11722 13638 16307



Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitud

...

2021-05-18 00:00:00
 [1]   206   572   791  1015  1479  1965  3015  4194  5537  7105  9019 10229
[13] 11722 13641 16314



Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitud

2021-05-18 00:00:00
 [1]   206   581   800  1023  1486  1971  3020  4198  5541  7109  9022 10232
[13] 11725 13643 16314



Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitud

2021-05-18 00:00:00
 [1]   206   588   806  1029  1491  1976  3023  4202  5545  7110  9026 10238
[13] 11728 13642 16309



In [7]:
for i in range(48):

    data = data.metpy.parse_cf()
    data_sfc = data_sfc.metpy.parse_cf()

    time = data['z'].metpy.time

    timeinit = time[0]
    timeinit = datetime.utcfromtimestamp(timeinit.item()/1e9)-timedelta(hours=1)
    print(timeinit)

    temp = data['t']
    qhum = data['q']
    uwind = data['u']
    vwind = data['v']
    geopot = data['z']
    press = data['level']

    sfctemp = data_sfc['t2m']
    sfcdew = data_sfc['d2m']
    pwat = data_sfc['tcwv']
    deg0l = data_sfc['deg0l']
    sfcpress =  data_sfc['sp']
    sfcuwind =  data_sfc['u10']
    sfcvwind =  data_sfc['v10']
    sfcgeopot =  data_sfc['z']

    ##############################################################

    lat = 49.7
    lon = 6.6

    #i = 0 # set time step

    temp = temp.metpy.loc[{'time': time[i], 'latitude': lat, 'longitude': lon}]
    sfctemp = sfctemp.metpy.loc[{'time': time[i], 'latitude': lat, 'longitude': lon}]
    sfcdew = sfcdew.metpy.loc[{'time': time[i], 'latitude': lat, 'longitude': lon}]
    sfcpress = sfcpress.metpy.loc[{'time': time[i], 'latitude': lat, 'longitude': lon}]
    sfcuwind = sfcuwind.metpy.loc[{'time': time[i], 'latitude': lat, 'longitude': lon}]
    sfcvwind = sfcvwind.metpy.loc[{'time': time[i], 'latitude': lat, 'longitude': lon}]
    sfcgeopot = sfcgeopot.metpy.loc[{'time': time[i], 'latitude': lat, 'longitude': lon}]
    qhum = qhum.metpy.loc[{'time': time[i], 'latitude': lat, 'longitude': lon}]
    geopot = geopot.metpy.loc[{'time': time[i], 'latitude': lat, 'longitude': lon}]
    uwind = uwind.metpy.loc[{'time': time[i], 'latitude': lat, 'longitude': lon}]
    vwind = vwind.metpy.loc[{'time': time[i], 'latitude': lat, 'longitude': lon}]
    pwat = pwat.metpy.loc[{'time': time[i], 'latitude': lat, 'longitude': lon}]
    deg0l = deg0l.metpy.loc[{'time': time[i], 'latitude': lat, 'longitude': lon}]

    temp[14] = sfctemp
    uwind[14] = sfcuwind
    vwind[14] = sfcvwind
    geopot[14] = sfcgeopot
    press = np.where(press==1000, sfcpress/100, press)
    
    #sfcpress.data=92000
    
    if sfcpress.item(0) <= 95200:
                temp = np.delete(temp,13)
                qhum = np.delete(qhum,13)
                geopot = np.delete(geopot,13)
                uwind = np.delete(uwind,13)
                vwind = np.delete(vwind,13)
                press = np.delete(press,13)
                
    if sfcpress.item(0) <= 92700:
                temp = np.delete(temp,12)
                qhum = np.delete(qhum,12)
                geopot = np.delete(geopot,12)
                uwind = np.delete(uwind,12)
                vwind = np.delete(vwind,12)
                press = np.delete(press,12)
    
    k = np.size(press)-3
    
    
    press = press[::-1]
    qhum = qhum.data[::-1]*units('kg/kg')
    uwind = uwind.data[::-1]
    vwind = vwind.data[::-1]
    geopot = geopot.data[::-1]*units('meters**2/second**2')
    temp = temp-273.15
    temp = temp.data[::-1]*units.degC

    dew = mpcalc.dewpoint_from_specific_humidity(press*units.hPa, temp, qhum)
    sfcdew = sfcdew.data.item()-273.15
    dew[0] = sfcdew*units.degC
    pwat = pwat.data.item()
    pwat = pwat*units.mm
    deg0l = deg0l.data.item()
    deg0l = deg0l*units.meters
    height = mpcalc.geopotential_to_height(geopot)


    # compute convective parameters
    ws = np.sqrt(uwind**2 + vwind**2)*1.94384
    ws = list(ws)
    pressure = list(press)
    temp2 = list(temp.magnitude)
    altitude = list(height.magnitude)
    dpt= list(dew.magnitude)
    wd = mpcalc.wind_direction(uwind* units('meters/second'), vwind* units('meters/second'), convention='from')
    wd = list(wd.magnitude)
    ws = robjects.IntVector(ws)
    wd = robjects.IntVector(wd)
    dpt = robjects.IntVector(dpt)
    altitude = robjects.IntVector(altitude)
    pressure = robjects.IntVector(pressure)
    temp2 = robjects.IntVector(temp2)
    print(altitude)
    time2 = str(i+1)
    robjects.r['sounding_save'](pressure,altitude,temp2,dpt,wd,ws, max_speed=30, filename='ecmwf_sounding_trier_%s.png' %time2,title='ECMWF | Trier | '+ timeinit.strftime('Init: %d.%m.%Y %H:%M UTC')
              + time[i].dt.strftime(' | Valid: %d.%m.%Y %H:%M UTC').item())

Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitud

2021-05-18 00:00:00
 [1]   307   534   753   977  1440  1926  2975  4154  5499  7077  9012 10216
[13] 11712 13639 16312



Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitud

2021-05-18 00:00:00
 [1]   307   539   758   981  1442  1927  2974  4150  5491  7065  9003 10213
[13] 11708 13630 16303



Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitud

...

2021-05-18 00:00:00
 [1]   307   567   787  1011  1474  1960  3011  4190  5534  7103  9012 10218
[13] 11711 13634 16311



Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitud

2021-05-18 00:00:00
 [1]   307   575   794  1017  1480  1965  3015  4194  5537  7105  9015 10222
[13] 11714 13636 16311



Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitud

2021-05-18 00:00:00
 [1]   307   582   800  1024  1485  1969  3018  4196  5540  7104  9017 10225
[13] 11717 13635 16306



In [8]:
for i in range(48):

    data = data.metpy.parse_cf()
    data_sfc = data_sfc.metpy.parse_cf()

    time = data['z'].metpy.time

    timeinit = time[0]
    timeinit = datetime.utcfromtimestamp(timeinit.item()/1e9)-timedelta(hours=1)
    print(timeinit)

    temp = data['t']
    qhum = data['q']
    uwind = data['u']
    vwind = data['v']
    geopot = data['z']
    press = data['level']

    sfctemp = data_sfc['t2m']
    sfcdew = data_sfc['d2m']
    pwat = data_sfc['tcwv']
    deg0l = data_sfc['deg0l']
    sfcpress =  data_sfc['sp']
    sfcuwind =  data_sfc['u10']
    sfcvwind =  data_sfc['v10']
    sfcgeopot =  data_sfc['z']

    ##############################################################

    lat = 49.7
    lon = 6.1

    #i = 0 # set time step

    temp = temp.metpy.loc[{'time': time[i], 'latitude': lat, 'longitude': lon}]
    sfctemp = sfctemp.metpy.loc[{'time': time[i], 'latitude': lat, 'longitude': lon}]
    sfcdew = sfcdew.metpy.loc[{'time': time[i], 'latitude': lat, 'longitude': lon}]
    sfcpress = sfcpress.metpy.loc[{'time': time[i], 'latitude': lat, 'longitude': lon}]
    sfcuwind = sfcuwind.metpy.loc[{'time': time[i], 'latitude': lat, 'longitude': lon}]
    sfcvwind = sfcvwind.metpy.loc[{'time': time[i], 'latitude': lat, 'longitude': lon}]
    sfcgeopot = sfcgeopot.metpy.loc[{'time': time[i], 'latitude': lat, 'longitude': lon}]
    qhum = qhum.metpy.loc[{'time': time[i], 'latitude': lat, 'longitude': lon}]
    geopot = geopot.metpy.loc[{'time': time[i], 'latitude': lat, 'longitude': lon}]
    uwind = uwind.metpy.loc[{'time': time[i], 'latitude': lat, 'longitude': lon}]
    vwind = vwind.metpy.loc[{'time': time[i], 'latitude': lat, 'longitude': lon}]
    pwat = pwat.metpy.loc[{'time': time[i], 'latitude': lat, 'longitude': lon}]
    deg0l = deg0l.metpy.loc[{'time': time[i], 'latitude': lat, 'longitude': lon}]

    temp[14] = sfctemp
    uwind[14] = sfcuwind
    vwind[14] = sfcvwind
    geopot[14] = sfcgeopot
    press = np.where(press==1000, sfcpress/100, press)
    
    #sfcpress.data=92000
    
    if sfcpress.item(0) <= 95200:
                temp = np.delete(temp,13)
                qhum = np.delete(qhum,13)
                geopot = np.delete(geopot,13)
                uwind = np.delete(uwind,13)
                vwind = np.delete(vwind,13)
                press = np.delete(press,13)
                
    if sfcpress.item(0) <= 92700:
                temp = np.delete(temp,12)
                qhum = np.delete(qhum,12)
                geopot = np.delete(geopot,12)
                uwind = np.delete(uwind,12)
                vwind = np.delete(vwind,12)
                press = np.delete(press,12)
    
    k = np.size(press)-3
    
    
    press = press[::-1]
    qhum = qhum.data[::-1]*units('kg/kg')
    uwind = uwind.data[::-1]
    vwind = vwind.data[::-1]
    geopot = geopot.data[::-1]*units('meters**2/second**2')
    temp = temp-273.15
    temp = temp.data[::-1]*units.degC

    dew = mpcalc.dewpoint_from_specific_humidity(press*units.hPa, temp, qhum)
    sfcdew = sfcdew.data.item()-273.15
    dew[0] = sfcdew*units.degC
    pwat = pwat.data.item()
    pwat = pwat*units.mm
    deg0l = deg0l.data.item()
    deg0l = deg0l*units.meters
    height = mpcalc.geopotential_to_height(geopot)


    # compute convective parameters
    ws = np.sqrt(uwind**2 + vwind**2)*1.94384
    ws = list(ws)
    pressure = list(press)
    temp2 = list(temp.magnitude)
    altitude = list(height.magnitude)
    dpt= list(dew.magnitude)
    wd = mpcalc.wind_direction(uwind* units('meters/second'), vwind* units('meters/second'), convention='from')
    wd = list(wd.magnitude)
    ws = robjects.IntVector(ws)
    wd = robjects.IntVector(wd)
    dpt = robjects.IntVector(dpt)
    altitude = robjects.IntVector(altitude)
    pressure = robjects.IntVector(pressure)
    temp2 = robjects.IntVector(temp2)
    print(altitude)
    time2 = str(i+1)
    robjects.r['sounding_save'](pressure,altitude,temp2,dpt,wd,ws, max_speed=30, filename='ecmwf_sounding_mersch_%s.png' %time2,title='ECMWF | Mersch | '+ timeinit.strftime('Init: %d.%m.%Y %H:%M UTC')
              + time[i].dt.strftime(' | Valid: %d.%m.%Y %H:%M UTC').item())

Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitud

2021-05-18 00:00:00
 [1]   318   534   753   976  1439  1924  2975  4154  5498  7074  9008 10215
[13] 11713 13638 16311



Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitud

2021-05-18 00:00:00
 [1]   318   539   757   980  1441  1926  2974  4149  5490  7062  8998 10212
[13] 11710 13629 16302



Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitud

...

2021-05-18 00:00:00
 [1]   318   569   788  1012  1475  1961  3011  4191  5534  7102  9014 10221
[13] 11714 13637 16312



Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitud

2021-05-18 00:00:00
 [1]   318   579   797  1020  1482  1967  3016  4196  5539  7106  9017 10226
[13] 11719 13640 16312



Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitud

2021-05-18 00:00:00
 [1]   318   586   803  1026  1488  1973  3022  4199  5543  7106  9020 10232
[13] 11723 13639 16307



In [9]:
for i in range(48):

    data = data.metpy.parse_cf()
    data_sfc = data_sfc.metpy.parse_cf()

    time = data['z'].metpy.time

    timeinit = time[0]
    timeinit = datetime.utcfromtimestamp(timeinit.item()/1e9)-timedelta(hours=1)
    print(timeinit)

    temp = data['t']
    qhum = data['q']
    uwind = data['u']
    vwind = data['v']
    geopot = data['z']
    press = data['level']

    sfctemp = data_sfc['t2m']
    sfcdew = data_sfc['d2m']
    pwat = data_sfc['tcwv']
    deg0l = data_sfc['deg0l']
    sfcpress =  data_sfc['sp']
    sfcuwind =  data_sfc['u10']
    sfcvwind =  data_sfc['v10']
    sfcgeopot =  data_sfc['z']

    ##############################################################

    lat = 49.7
    lon = 5.6

    #i = 0 # set time step

    temp = temp.metpy.loc[{'time': time[i], 'latitude': lat, 'longitude': lon}]
    sfctemp = sfctemp.metpy.loc[{'time': time[i], 'latitude': lat, 'longitude': lon}]
    sfcdew = sfcdew.metpy.loc[{'time': time[i], 'latitude': lat, 'longitude': lon}]
    sfcpress = sfcpress.metpy.loc[{'time': time[i], 'latitude': lat, 'longitude': lon}]
    sfcuwind = sfcuwind.metpy.loc[{'time': time[i], 'latitude': lat, 'longitude': lon}]
    sfcvwind = sfcvwind.metpy.loc[{'time': time[i], 'latitude': lat, 'longitude': lon}]
    sfcgeopot = sfcgeopot.metpy.loc[{'time': time[i], 'latitude': lat, 'longitude': lon}]
    qhum = qhum.metpy.loc[{'time': time[i], 'latitude': lat, 'longitude': lon}]
    geopot = geopot.metpy.loc[{'time': time[i], 'latitude': lat, 'longitude': lon}]
    uwind = uwind.metpy.loc[{'time': time[i], 'latitude': lat, 'longitude': lon}]
    vwind = vwind.metpy.loc[{'time': time[i], 'latitude': lat, 'longitude': lon}]
    pwat = pwat.metpy.loc[{'time': time[i], 'latitude': lat, 'longitude': lon}]
    deg0l = deg0l.metpy.loc[{'time': time[i], 'latitude': lat, 'longitude': lon}]

    temp[14] = sfctemp
    uwind[14] = sfcuwind
    vwind[14] = sfcvwind
    geopot[14] = sfcgeopot
    press = np.where(press==1000, sfcpress/100, press)
    
    #sfcpress.data=92000
    
    if sfcpress.item(0) <= 95200:
                temp = np.delete(temp,13)
                qhum = np.delete(qhum,13)
                geopot = np.delete(geopot,13)
                uwind = np.delete(uwind,13)
                vwind = np.delete(vwind,13)
                press = np.delete(press,13)
                
    if sfcpress.item(0) <= 92700:
                temp = np.delete(temp,12)
                qhum = np.delete(qhum,12)
                geopot = np.delete(geopot,12)
                uwind = np.delete(uwind,12)
                vwind = np.delete(vwind,12)
                press = np.delete(press,12)
    
    k = np.size(press)-3
    
    
    press = press[::-1]
    qhum = qhum.data[::-1]*units('kg/kg')
    uwind = uwind.data[::-1]
    vwind = vwind.data[::-1]
    geopot = geopot.data[::-1]*units('meters**2/second**2')
    temp = temp-273.15
    temp = temp.data[::-1]*units.degC

    dew = mpcalc.dewpoint_from_specific_humidity(press*units.hPa, temp, qhum)
    sfcdew = sfcdew.data.item()-273.15
    dew[0] = sfcdew*units.degC
    pwat = pwat.data.item()
    pwat = pwat*units.mm
    deg0l = deg0l.data.item()
    deg0l = deg0l*units.meters
    height = mpcalc.geopotential_to_height(geopot)


    # compute convective parameters
    ws = np.sqrt(uwind**2 + vwind**2)*1.94384
    ws = list(ws)
    pressure = list(press)
    temp2 = list(temp.magnitude)
    altitude = list(height.magnitude)
    dpt= list(dew.magnitude)
    wd = mpcalc.wind_direction(uwind* units('meters/second'), vwind* units('meters/second'), convention='from')
    wd = list(wd.magnitude)
    ws = robjects.IntVector(ws)
    wd = robjects.IntVector(wd)
    dpt = robjects.IntVector(dpt)
    altitude = robjects.IntVector(altitude)
    pressure = robjects.IntVector(pressure)
    temp2 = robjects.IntVector(temp2)
    print(altitude)
    time2 = str(i+1)
    robjects.r['sounding_save'](pressure,altitude,temp2,dpt,wd,ws, max_speed=30, filename='ecmwf_sounding_habay_%s.png' %time2,title='ECMWF | Habay | '+ timeinit.strftime('Init: %d.%m.%Y %H:%M UTC')
              + time[i].dt.strftime(' | Valid: %d.%m.%Y %H:%M UTC').item())

Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitud

2021-05-18 00:00:00
 [1]   372   535   753   976  1439  1923  2973  4151  5496  7072  9006 10213
[13] 11712 13638 16308



Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitud

2021-05-18 00:00:00
 [1]   372   539   757   980  1441  1925  2973  4147  5488  7061  8995 10209
[13] 11707 13629 16300



Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitud

...

2021-05-18 00:00:00
 [1]   372   573   792  1015  1478  1963  3013  4192  5534  7102  9017 10225
[13] 11718 13639 16314



Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitud

2021-05-18 00:00:00
 [1]   372   582   800  1023  1486  1971  3020  4198  5542  7107  9022 10232
[13] 11723 13643 16313



Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitud

2021-05-18 00:00:00
 [1]   372   590   807  1030  1492  1977  3026  4203  5546  7108  9026 10240
[13] 11729 13643 16309



In [10]:
for i in range(48):

    data = data.metpy.parse_cf()
    data_sfc = data_sfc.metpy.parse_cf()

    time = data['z'].metpy.time

    timeinit = time[0]
    timeinit = datetime.utcfromtimestamp(timeinit.item()/1e9)-timedelta(hours=1)
    print(timeinit)

    temp = data['t']
    qhum = data['q']
    uwind = data['u']
    vwind = data['v']
    geopot = data['z']
    press = data['level']

    sfctemp = data_sfc['t2m']
    sfcdew = data_sfc['d2m']
    pwat = data_sfc['tcwv']
    deg0l = data_sfc['deg0l']
    sfcpress =  data_sfc['sp']
    sfcuwind =  data_sfc['u10']
    sfcvwind =  data_sfc['v10']
    sfcgeopot =  data_sfc['z']

    ##############################################################

    lat = 49.5
    lon = 5.8

    #i = 0 # set time step

    temp = temp.metpy.loc[{'time': time[i], 'latitude': lat, 'longitude': lon}]
    sfctemp = sfctemp.metpy.loc[{'time': time[i], 'latitude': lat, 'longitude': lon}]
    sfcdew = sfcdew.metpy.loc[{'time': time[i], 'latitude': lat, 'longitude': lon}]
    sfcpress = sfcpress.metpy.loc[{'time': time[i], 'latitude': lat, 'longitude': lon}]
    sfcuwind = sfcuwind.metpy.loc[{'time': time[i], 'latitude': lat, 'longitude': lon}]
    sfcvwind = sfcvwind.metpy.loc[{'time': time[i], 'latitude': lat, 'longitude': lon}]
    sfcgeopot = sfcgeopot.metpy.loc[{'time': time[i], 'latitude': lat, 'longitude': lon}]
    qhum = qhum.metpy.loc[{'time': time[i], 'latitude': lat, 'longitude': lon}]
    geopot = geopot.metpy.loc[{'time': time[i], 'latitude': lat, 'longitude': lon}]
    uwind = uwind.metpy.loc[{'time': time[i], 'latitude': lat, 'longitude': lon}]
    vwind = vwind.metpy.loc[{'time': time[i], 'latitude': lat, 'longitude': lon}]
    pwat = pwat.metpy.loc[{'time': time[i], 'latitude': lat, 'longitude': lon}]
    deg0l = deg0l.metpy.loc[{'time': time[i], 'latitude': lat, 'longitude': lon}]

    temp[14] = sfctemp
    uwind[14] = sfcuwind
    vwind[14] = sfcvwind
    geopot[14] = sfcgeopot
    press = np.where(press==1000, sfcpress/100, press)
    
    #sfcpress.data=92000
    
    if sfcpress.item(0) <= 95200:
                temp = np.delete(temp,13)
                qhum = np.delete(qhum,13)
                geopot = np.delete(geopot,13)
                uwind = np.delete(uwind,13)
                vwind = np.delete(vwind,13)
                press = np.delete(press,13)
                
    if sfcpress.item(0) <= 92700:
                temp = np.delete(temp,12)
                qhum = np.delete(qhum,12)
                geopot = np.delete(geopot,12)
                uwind = np.delete(uwind,12)
                vwind = np.delete(vwind,12)
                press = np.delete(press,12)
    
    k = np.size(press)-3
    
    
    press = press[::-1]
    qhum = qhum.data[::-1]*units('kg/kg')
    uwind = uwind.data[::-1]
    vwind = vwind.data[::-1]
    geopot = geopot.data[::-1]*units('meters**2/second**2')
    temp = temp-273.15
    temp = temp.data[::-1]*units.degC

    dew = mpcalc.dewpoint_from_specific_humidity(press*units.hPa, temp, qhum)
    sfcdew = sfcdew.data.item()-273.15
    dew[0] = sfcdew*units.degC
    pwat = pwat.data.item()
    pwat = pwat*units.mm
    deg0l = deg0l.data.item()
    deg0l = deg0l*units.meters
    height = mpcalc.geopotential_to_height(geopot)


    # compute convective parameters
    ws = np.sqrt(uwind**2 + vwind**2)*1.94384
    ws = list(ws)
    pressure = list(press)
    temp2 = list(temp.magnitude)
    altitude = list(height.magnitude)
    dpt= list(dew.magnitude)
    wd = mpcalc.wind_direction(uwind* units('meters/second'), vwind* units('meters/second'), convention='from')
    wd = list(wd.magnitude)
    ws = robjects.IntVector(ws)
    wd = robjects.IntVector(wd)
    dpt = robjects.IntVector(dpt)
    altitude = robjects.IntVector(altitude)
    pressure = robjects.IntVector(pressure)
    temp2 = robjects.IntVector(temp2)
    print(altitude)
    time2 = str(i+1)
    robjects.r['sounding_save'](pressure,altitude,temp2,dpt,wd,ws, max_speed=30, filename='ecmwf_sounding_longwy_%s.png' %time2,title='ECMWF | Longwy | '+ timeinit.strftime('Init: %d.%m.%Y %H:%M UTC')
              + time[i].dt.strftime(' | Valid: %d.%m.%Y %H:%M UTC').item())

Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitud

2021-05-18 00:00:00
 [1]   351   537   756   979  1442  1927  2977  4156  5501  7077  9011 10219
[13] 11718 13642 16311



Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitud

2021-05-18 00:00:00
 [1]   351   542   760   983  1444  1928  2976  4151  5492  7065  9001 10215
[13] 11714 13634 16303



Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitud

...

2021-05-18 00:00:00
 [1]   351   573   792  1015  1478  1964  3014  4193  5535  7103  9019 10227
[13] 11720 13641 16314



Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitud

2021-05-18 00:00:00
 [1]   351   583   801  1024  1486  1971  3020  4199  5542  7109  9023 10233
[13] 11725 13644 16314



Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitud

2021-05-18 00:00:00
 [1]   351   590   808  1031  1492  1977  3025  4202  5546  7109  9027 10240
[13] 11730 13644 16309



In [11]:
for i in range(48):

    data = data.metpy.parse_cf()
    data_sfc = data_sfc.metpy.parse_cf()

    time = data['z'].metpy.time

    timeinit = time[0]
    timeinit = datetime.utcfromtimestamp(timeinit.item()/1e9)-timedelta(hours=1)
    print(timeinit)

    temp = data['t']
    qhum = data['q']
    uwind = data['u']
    vwind = data['v']
    geopot = data['z']
    press = data['level']

    sfctemp = data_sfc['t2m']
    sfcdew = data_sfc['d2m']
    pwat = data_sfc['tcwv']
    deg0l = data_sfc['deg0l']
    sfcpress =  data_sfc['sp']
    sfcuwind =  data_sfc['u10']
    sfcvwind =  data_sfc['v10']
    sfcgeopot =  data_sfc['z']

    ##############################################################

    lat = 50.0
    lon = 5.4

    #i = 0 # set time step

    temp = temp.metpy.loc[{'time': time[i], 'latitude': lat, 'longitude': lon}]
    sfctemp = sfctemp.metpy.loc[{'time': time[i], 'latitude': lat, 'longitude': lon}]
    sfcdew = sfcdew.metpy.loc[{'time': time[i], 'latitude': lat, 'longitude': lon}]
    sfcpress = sfcpress.metpy.loc[{'time': time[i], 'latitude': lat, 'longitude': lon}]
    sfcuwind = sfcuwind.metpy.loc[{'time': time[i], 'latitude': lat, 'longitude': lon}]
    sfcvwind = sfcvwind.metpy.loc[{'time': time[i], 'latitude': lat, 'longitude': lon}]
    sfcgeopot = sfcgeopot.metpy.loc[{'time': time[i], 'latitude': lat, 'longitude': lon}]
    qhum = qhum.metpy.loc[{'time': time[i], 'latitude': lat, 'longitude': lon}]
    geopot = geopot.metpy.loc[{'time': time[i], 'latitude': lat, 'longitude': lon}]
    uwind = uwind.metpy.loc[{'time': time[i], 'latitude': lat, 'longitude': lon}]
    vwind = vwind.metpy.loc[{'time': time[i], 'latitude': lat, 'longitude': lon}]
    pwat = pwat.metpy.loc[{'time': time[i], 'latitude': lat, 'longitude': lon}]
    deg0l = deg0l.metpy.loc[{'time': time[i], 'latitude': lat, 'longitude': lon}]

    temp[14] = sfctemp
    uwind[14] = sfcuwind
    vwind[14] = sfcvwind
    geopot[14] = sfcgeopot
    press = np.where(press==1000, sfcpress/100, press)
    
    #sfcpress.data=92000
    
    if sfcpress.item(0) <= 95200:
                temp = np.delete(temp,13)
                qhum = np.delete(qhum,13)
                geopot = np.delete(geopot,13)
                uwind = np.delete(uwind,13)
                vwind = np.delete(vwind,13)
                press = np.delete(press,13)
                
    if sfcpress.item(0) <= 92700:
                temp = np.delete(temp,12)
                qhum = np.delete(qhum,12)
                geopot = np.delete(geopot,12)
                uwind = np.delete(uwind,12)
                vwind = np.delete(vwind,12)
                press = np.delete(press,12)
    
    k = np.size(press)-3
    
    
    press = press[::-1]
    qhum = qhum.data[::-1]*units('kg/kg')
    uwind = uwind.data[::-1]
    vwind = vwind.data[::-1]
    geopot = geopot.data[::-1]*units('meters**2/second**2')
    temp = temp-273.15
    temp = temp.data[::-1]*units.degC

    dew = mpcalc.dewpoint_from_specific_humidity(press*units.hPa, temp, qhum)
    sfcdew = sfcdew.data.item()-273.15
    dew[0] = sfcdew*units.degC
    pwat = pwat.data.item()
    pwat = pwat*units.mm
    deg0l = deg0l.data.item()
    deg0l = deg0l*units.meters
    height = mpcalc.geopotential_to_height(geopot)


    # compute convective parameters
    ws = np.sqrt(uwind**2 + vwind**2)*1.94384
    ws = list(ws)
    pressure = list(press)
    temp2 = list(temp.magnitude)
    altitude = list(height.magnitude)
    dpt= list(dew.magnitude)
    wd = mpcalc.wind_direction(uwind* units('meters/second'), vwind* units('meters/second'), convention='from')
    wd = list(wd.magnitude)
    ws = robjects.IntVector(ws)
    wd = robjects.IntVector(wd)
    dpt = robjects.IntVector(dpt)
    altitude = robjects.IntVector(altitude)
    pressure = robjects.IntVector(pressure)
    temp2 = robjects.IntVector(temp2)
    print(altitude)
    time2 = str(i+1)
    robjects.r['sounding_save'](pressure,altitude,temp2,dpt,wd,ws, max_speed=30, filename='ecmwf_sounding_sthubert_%s.png' %time2,title='ECMWF | Saint-Hubert | '+ timeinit.strftime('Init: %d.%m.%Y %H:%M UTC')
              + time[i].dt.strftime(' | Valid: %d.%m.%Y %H:%M UTC').item())

Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitud

2021-05-18 00:00:00
 [1]   468   531   749   972  1434  1919  2967  4145  5490  7065  8998 10204
[13] 11702 13631 16303



Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitud

2021-05-18 00:00:00
 [1]   468   534   752   975  1436  1920  2968  4143  5485  7057  8987 10201
[13] 11698 13622 16295



Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitud

...

2021-05-18 00:00:00
 [1]   468   573   792  1015  1477  1961  3011  4190  5534  7100  9013 10220
[13] 11714 13636 16312



Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitud

2021-05-18 00:00:00
 [1]   468   582   801  1023  1485  1969  3019  4197  5542  7105  9018 10228
[13] 11721 13641 16312



Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitud

2021-05-18 00:00:00
 [1]   468   589   807  1030  1491  1975  3024  4203  5546  7106  9022 10237
[13] 11727 13641 16308



In [12]:
for i in range(48):

    data = data.metpy.parse_cf()
    data_sfc = data_sfc.metpy.parse_cf()

    time = data['z'].metpy.time

    timeinit = time[0]
    timeinit = datetime.utcfromtimestamp(timeinit.item()/1e9)-timedelta(hours=1)
    print(timeinit)

    temp = data['t']
    qhum = data['q']
    uwind = data['u']
    vwind = data['v']
    geopot = data['z']
    press = data['level']

    sfctemp = data_sfc['t2m']
    sfcdew = data_sfc['d2m']
    pwat = data_sfc['tcwv']
    deg0l = data_sfc['deg0l']
    sfcpress =  data_sfc['sp']
    sfcuwind =  data_sfc['u10']
    sfcvwind =  data_sfc['v10']
    sfcgeopot =  data_sfc['z']

    ##############################################################

    lat = 50.0
    lon = 6.5

    #i = 0 # set time step

    temp = temp.metpy.loc[{'time': time[i], 'latitude': lat, 'longitude': lon}]
    sfctemp = sfctemp.metpy.loc[{'time': time[i], 'latitude': lat, 'longitude': lon}]
    sfcdew = sfcdew.metpy.loc[{'time': time[i], 'latitude': lat, 'longitude': lon}]
    sfcpress = sfcpress.metpy.loc[{'time': time[i], 'latitude': lat, 'longitude': lon}]
    sfcuwind = sfcuwind.metpy.loc[{'time': time[i], 'latitude': lat, 'longitude': lon}]
    sfcvwind = sfcvwind.metpy.loc[{'time': time[i], 'latitude': lat, 'longitude': lon}]
    sfcgeopot = sfcgeopot.metpy.loc[{'time': time[i], 'latitude': lat, 'longitude': lon}]
    qhum = qhum.metpy.loc[{'time': time[i], 'latitude': lat, 'longitude': lon}]
    geopot = geopot.metpy.loc[{'time': time[i], 'latitude': lat, 'longitude': lon}]
    uwind = uwind.metpy.loc[{'time': time[i], 'latitude': lat, 'longitude': lon}]
    vwind = vwind.metpy.loc[{'time': time[i], 'latitude': lat, 'longitude': lon}]
    pwat = pwat.metpy.loc[{'time': time[i], 'latitude': lat, 'longitude': lon}]
    deg0l = deg0l.metpy.loc[{'time': time[i], 'latitude': lat, 'longitude': lon}]

    temp[14] = sfctemp
    uwind[14] = sfcuwind
    vwind[14] = sfcvwind
    geopot[14] = sfcgeopot
    press = np.where(press==1000, sfcpress/100, press)
    
    #sfcpress.data=92000
    
    if sfcpress.item(0) <= 95200:
                temp = np.delete(temp,13)
                qhum = np.delete(qhum,13)
                geopot = np.delete(geopot,13)
                uwind = np.delete(uwind,13)
                vwind = np.delete(vwind,13)
                press = np.delete(press,13)
                
    if sfcpress.item(0) <= 92700:
                temp = np.delete(temp,12)
                qhum = np.delete(qhum,12)
                geopot = np.delete(geopot,12)
                uwind = np.delete(uwind,12)
                vwind = np.delete(vwind,12)
                press = np.delete(press,12)
    
    k = np.size(press)-3
    
    
    press = press[::-1]
    qhum = qhum.data[::-1]*units('kg/kg')
    uwind = uwind.data[::-1]
    vwind = vwind.data[::-1]
    geopot = geopot.data[::-1]*units('meters**2/second**2')
    temp = temp-273.15
    temp = temp.data[::-1]*units.degC

    dew = mpcalc.dewpoint_from_specific_humidity(press*units.hPa, temp, qhum)
    sfcdew = sfcdew.data.item()-273.15
    dew[0] = sfcdew*units.degC
    pwat = pwat.data.item()
    pwat = pwat*units.mm
    deg0l = deg0l.data.item()
    deg0l = deg0l*units.meters
    height = mpcalc.geopotential_to_height(geopot)


    # compute convective parameters
    ws = np.sqrt(uwind**2 + vwind**2)*1.94384
    ws = list(ws)
    pressure = list(press)
    temp2 = list(temp.magnitude)
    altitude = list(height.magnitude)
    dpt= list(dew.magnitude)
    wd = mpcalc.wind_direction(uwind* units('meters/second'), vwind* units('meters/second'), convention='from')
    wd = list(wd.magnitude)
    ws = robjects.IntVector(ws)
    wd = robjects.IntVector(wd)
    dpt = robjects.IntVector(dpt)
    altitude = robjects.IntVector(altitude)
    pressure = robjects.IntVector(pressure)
    temp2 = robjects.IntVector(temp2)
    print(altitude)
    time2 = str(i+1)
    robjects.r['sounding_save'](pressure,altitude,temp2,dpt,wd,ws, max_speed=30, filename='ecmwf_sounding_bitburg_%s.png' %time2,title='ECMWF | Bitburg | '+ timeinit.strftime('Init: %d.%m.%Y %H:%M UTC')
              + time[i].dt.strftime(' | Valid: %d.%m.%Y %H:%M UTC').item())

Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitud

2021-05-18 00:00:00
 [1]   368   530   748   972  1434  1920  2970  4149  5494  7071  9004 10207
[13] 11704 13632 16306



Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitud

2021-05-18 00:00:00
 [1]   368   534   752   975  1437  1921  2969  4145  5487  7061  8994 10204
[13] 11702 13624 16298



Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitud

...

2021-05-18 00:00:00
 [1]   368   566   785  1009  1472  1958  3009  4188  5532  7101  9009 10213
[13] 11707 13631 16308



Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitud

2021-05-18 00:00:00
 [1]   368   574   793  1016  1479  1964  3014  4192  5536  7103  9011 10217
[13] 11711 13633 16309



Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitud

2021-05-18 00:00:00
 [1]   368   580   799  1022  1483  1968  3018  4195  5539  7102  9013 10221
[13] 11714 13633 16305



In [13]:
for i in range(48):

    data = data.metpy.parse_cf()
    data_sfc = data_sfc.metpy.parse_cf()

    time = data['z'].metpy.time

    timeinit = time[0]
    timeinit = datetime.utcfromtimestamp(timeinit.item()/1e9)-timedelta(hours=1)
    print(timeinit)

    temp = data['t']
    qhum = data['q']
    uwind = data['u']
    vwind = data['v']
    geopot = data['z']
    press = data['level']

    sfctemp = data_sfc['t2m']
    sfcdew = data_sfc['d2m']
    pwat = data_sfc['tcwv']
    deg0l = data_sfc['deg0l']
    sfcpress =  data_sfc['sp']
    sfcuwind =  data_sfc['u10']
    sfcvwind =  data_sfc['v10']
    sfcgeopot =  data_sfc['z']

    ##############################################################

    lat = 49.5
    lon = 6.6

    #i = 0 # set time step

    temp = temp.metpy.loc[{'time': time[i], 'latitude': lat, 'longitude': lon}]
    sfctemp = sfctemp.metpy.loc[{'time': time[i], 'latitude': lat, 'longitude': lon}]
    sfcdew = sfcdew.metpy.loc[{'time': time[i], 'latitude': lat, 'longitude': lon}]
    sfcpress = sfcpress.metpy.loc[{'time': time[i], 'latitude': lat, 'longitude': lon}]
    sfcuwind = sfcuwind.metpy.loc[{'time': time[i], 'latitude': lat, 'longitude': lon}]
    sfcvwind = sfcvwind.metpy.loc[{'time': time[i], 'latitude': lat, 'longitude': lon}]
    sfcgeopot = sfcgeopot.metpy.loc[{'time': time[i], 'latitude': lat, 'longitude': lon}]
    qhum = qhum.metpy.loc[{'time': time[i], 'latitude': lat, 'longitude': lon}]
    geopot = geopot.metpy.loc[{'time': time[i], 'latitude': lat, 'longitude': lon}]
    uwind = uwind.metpy.loc[{'time': time[i], 'latitude': lat, 'longitude': lon}]
    vwind = vwind.metpy.loc[{'time': time[i], 'latitude': lat, 'longitude': lon}]
    pwat = pwat.metpy.loc[{'time': time[i], 'latitude': lat, 'longitude': lon}]
    deg0l = deg0l.metpy.loc[{'time': time[i], 'latitude': lat, 'longitude': lon}]

    temp[14] = sfctemp
    uwind[14] = sfcuwind
    vwind[14] = sfcvwind
    geopot[14] = sfcgeopot
    press = np.where(press==1000, sfcpress/100, press)
    
    #sfcpress.data=92000
    
    if sfcpress.item(0) <= 95200:
                temp = np.delete(temp,13)
                qhum = np.delete(qhum,13)
                geopot = np.delete(geopot,13)
                uwind = np.delete(uwind,13)
                vwind = np.delete(vwind,13)
                press = np.delete(press,13)
                
    if sfcpress.item(0) <= 92700:
                temp = np.delete(temp,12)
                qhum = np.delete(qhum,12)
                geopot = np.delete(geopot,12)
                uwind = np.delete(uwind,12)
                vwind = np.delete(vwind,12)
                press = np.delete(press,12)
    
    k = np.size(press)-3
    
    
    press = press[::-1]
    qhum = qhum.data[::-1]*units('kg/kg')
    uwind = uwind.data[::-1]
    vwind = vwind.data[::-1]
    geopot = geopot.data[::-1]*units('meters**2/second**2')
    temp = temp-273.15
    temp = temp.data[::-1]*units.degC

    dew = mpcalc.dewpoint_from_specific_humidity(press*units.hPa, temp, qhum)
    sfcdew = sfcdew.data.item()-273.15
    dew[0] = sfcdew*units.degC
    pwat = pwat.data.item()
    pwat = pwat*units.mm
    deg0l = deg0l.data.item()
    deg0l = deg0l*units.meters
    height = mpcalc.geopotential_to_height(geopot)


    # compute convective parameters
    ws = np.sqrt(uwind**2 + vwind**2)*1.94384
    ws = list(ws)
    pressure = list(press)
    temp2 = list(temp.magnitude)
    altitude = list(height.magnitude)
    dpt= list(dew.magnitude)
    wd = mpcalc.wind_direction(uwind* units('meters/second'), vwind* units('meters/second'), convention='from')
    wd = list(wd.magnitude)
    ws = robjects.IntVector(ws)
    wd = robjects.IntVector(wd)
    dpt = robjects.IntVector(dpt)
    altitude = robjects.IntVector(altitude)
    pressure = robjects.IntVector(pressure)
    temp2 = robjects.IntVector(temp2)
    print(altitude)
    time2 = str(i+1)
    robjects.r['sounding_save'](pressure,altitude,temp2,dpt,wd,ws, max_speed=30, filename='ecmwf_sounding_mettlach_%s.png' %time2,title='ECMWF | Mettlach | '+ timeinit.strftime('Init: %d.%m.%Y %H:%M UTC')
              + time[i].dt.strftime(' | Valid: %d.%m.%Y %H:%M UTC').item())

Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitud

2021-05-18 00:00:00
 [1]   316   537   756   980  1443  1929  2979  4157  5503  7081  9017 10222
[13] 11718 13643 16315



Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitud

2021-05-18 00:00:00
 [1]   316   542   760   983  1445  1930  2978  4154  5495  7068  9008 10219
[13] 11713 13634 16306



Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitud

...

2021-05-18 00:00:00
 [1]   316   569   788  1012  1476  1962  3013  4192  5535  7104  9014 10222
[13] 11715 13636 16312



Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitud

2021-05-18 00:00:00
 [1]   316   576   795  1018  1481  1966  3016  4195  5538  7106  9017 10225
[13] 11717 13639 16311



Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitud

2021-05-18 00:00:00
 [1]   316   583   801  1024  1486  1970  3019  4198  5541  7106  9019 10228
[13] 11720 13637 16307



In [14]:
for i in range(48):

    data = data.metpy.parse_cf()
    data_sfc = data_sfc.metpy.parse_cf()

    time = data['z'].metpy.time

    timeinit = time[0]
    timeinit = datetime.utcfromtimestamp(timeinit.item()/1e9)-timedelta(hours=1)
    print(timeinit)

    temp = data['t']
    qhum = data['q']
    uwind = data['u']
    vwind = data['v']
    geopot = data['z']
    press = data['level']

    sfctemp = data_sfc['t2m']
    sfcdew = data_sfc['d2m']
    pwat = data_sfc['tcwv']
    deg0l = data_sfc['deg0l']
    sfcpress =  data_sfc['sp']
    sfcuwind =  data_sfc['u10']
    sfcvwind =  data_sfc['v10']
    sfcgeopot =  data_sfc['z']

    ##############################################################

    lat = 49.2
    lon = 5.4

    #i = 0 # set time step

    temp = temp.metpy.loc[{'time': time[i], 'latitude': lat, 'longitude': lon}]
    sfctemp = sfctemp.metpy.loc[{'time': time[i], 'latitude': lat, 'longitude': lon}]
    sfcdew = sfcdew.metpy.loc[{'time': time[i], 'latitude': lat, 'longitude': lon}]
    sfcpress = sfcpress.metpy.loc[{'time': time[i], 'latitude': lat, 'longitude': lon}]
    sfcuwind = sfcuwind.metpy.loc[{'time': time[i], 'latitude': lat, 'longitude': lon}]
    sfcvwind = sfcvwind.metpy.loc[{'time': time[i], 'latitude': lat, 'longitude': lon}]
    sfcgeopot = sfcgeopot.metpy.loc[{'time': time[i], 'latitude': lat, 'longitude': lon}]
    qhum = qhum.metpy.loc[{'time': time[i], 'latitude': lat, 'longitude': lon}]
    geopot = geopot.metpy.loc[{'time': time[i], 'latitude': lat, 'longitude': lon}]
    uwind = uwind.metpy.loc[{'time': time[i], 'latitude': lat, 'longitude': lon}]
    vwind = vwind.metpy.loc[{'time': time[i], 'latitude': lat, 'longitude': lon}]
    pwat = pwat.metpy.loc[{'time': time[i], 'latitude': lat, 'longitude': lon}]
    deg0l = deg0l.metpy.loc[{'time': time[i], 'latitude': lat, 'longitude': lon}]

    temp[14] = sfctemp
    uwind[14] = sfcuwind
    vwind[14] = sfcvwind
    geopot[14] = sfcgeopot
    press = np.where(press==1000, sfcpress/100, press)
    
    #sfcpress.data=92000
    
    if sfcpress.item(0) <= 95200:
                temp = np.delete(temp,13)
                qhum = np.delete(qhum,13)
                geopot = np.delete(geopot,13)
                uwind = np.delete(uwind,13)
                vwind = np.delete(vwind,13)
                press = np.delete(press,13)
                
    if sfcpress.item(0) <= 92700:
                temp = np.delete(temp,12)
                qhum = np.delete(qhum,12)
                geopot = np.delete(geopot,12)
                uwind = np.delete(uwind,12)
                vwind = np.delete(vwind,12)
                press = np.delete(press,12)
    
    k = np.size(press)-3
    
    
    press = press[::-1]
    qhum = qhum.data[::-1]*units('kg/kg')
    uwind = uwind.data[::-1]
    vwind = vwind.data[::-1]
    geopot = geopot.data[::-1]*units('meters**2/second**2')
    temp = temp-273.15
    temp = temp.data[::-1]*units.degC

    dew = mpcalc.dewpoint_from_specific_humidity(press*units.hPa, temp, qhum)
    sfcdew = sfcdew.data.item()-273.15
    dew[0] = sfcdew*units.degC
    pwat = pwat.data.item()
    pwat = pwat*units.mm
    deg0l = deg0l.data.item()
    deg0l = deg0l*units.meters
    height = mpcalc.geopotential_to_height(geopot)


    # compute convective parameters
    ws = np.sqrt(uwind**2 + vwind**2)*1.94384
    ws = list(ws)
    pressure = list(press)
    temp2 = list(temp.magnitude)
    altitude = list(height.magnitude)
    dpt= list(dew.magnitude)
    wd = mpcalc.wind_direction(uwind* units('meters/second'), vwind* units('meters/second'), convention='from')
    wd = list(wd.magnitude)
    ws = robjects.IntVector(ws)
    wd = robjects.IntVector(wd)
    dpt = robjects.IntVector(dpt)
    altitude = robjects.IntVector(altitude)
    pressure = robjects.IntVector(pressure)
    temp2 = robjects.IntVector(temp2)
    print(altitude)
    time2 = str(i+1)
    robjects.r['sounding_save'](pressure,altitude,temp2,dpt,wd,ws, max_speed=30, filename='ecmwf_sounding_verdun_%s.png' %time2,title='ECMWF | Verdun | '+ timeinit.strftime('Init: %d.%m.%Y %H:%M UTC')
              + time[i].dt.strftime(' | Valid: %d.%m.%Y %H:%M UTC').item())

Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitud

2021-05-18 00:00:00
 [1]   266   542   761   985  1448  1932  2982  4160  5503  7079  9018 10227
[13] 11727 13649 16313



Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitud

2021-05-18 00:00:00
 [1]   266   546   764   987  1449  1933  2980  4155  5495  7070  9010 10224
[13] 11721 13640 16306



Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitud

...

2021-05-18 00:00:00
 [1]   266   579   797  1021  1484  1969  3019  4197  5539  7107  9026 10239
[13] 11729 13648 16318



Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitud

2021-05-18 00:00:00
 [1]   266   588   806  1030  1492  1977  3026  4204  5546  7113  9032 10245
[13] 11735 13650 16318



Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitud

2021-05-18 00:00:00
 [1]   266   595   814  1037  1498  1982  3031  4208  5550  7115  9040 10254
[13] 11741 13651 16314



In [15]:
for i in range(48):

    data = data.metpy.parse_cf()
    data_sfc = data_sfc.metpy.parse_cf()

    time = data['z'].metpy.time

    timeinit = time[0]
    timeinit = datetime.utcfromtimestamp(timeinit.item()/1e9)-timedelta(hours=1)
    print(timeinit)

    temp = data['t']
    qhum = data['q']
    uwind = data['u']
    vwind = data['v']
    geopot = data['z']
    press = data['level']

    sfctemp = data_sfc['t2m']
    sfcdew = data_sfc['d2m']
    pwat = data_sfc['tcwv']
    deg0l = data_sfc['deg0l']
    sfcpress =  data_sfc['sp']
    sfcuwind =  data_sfc['u10']
    sfcvwind =  data_sfc['v10']
    sfcgeopot =  data_sfc['z']

    ##############################################################

    lat = 49.5
    lon = 5.2

    #i = 0 # set time step

    temp = temp.metpy.loc[{'time': time[i], 'latitude': lat, 'longitude': lon}]
    sfctemp = sfctemp.metpy.loc[{'time': time[i], 'latitude': lat, 'longitude': lon}]
    sfcdew = sfcdew.metpy.loc[{'time': time[i], 'latitude': lat, 'longitude': lon}]
    sfcpress = sfcpress.metpy.loc[{'time': time[i], 'latitude': lat, 'longitude': lon}]
    sfcuwind = sfcuwind.metpy.loc[{'time': time[i], 'latitude': lat, 'longitude': lon}]
    sfcvwind = sfcvwind.metpy.loc[{'time': time[i], 'latitude': lat, 'longitude': lon}]
    sfcgeopot = sfcgeopot.metpy.loc[{'time': time[i], 'latitude': lat, 'longitude': lon}]
    qhum = qhum.metpy.loc[{'time': time[i], 'latitude': lat, 'longitude': lon}]
    geopot = geopot.metpy.loc[{'time': time[i], 'latitude': lat, 'longitude': lon}]
    uwind = uwind.metpy.loc[{'time': time[i], 'latitude': lat, 'longitude': lon}]
    vwind = vwind.metpy.loc[{'time': time[i], 'latitude': lat, 'longitude': lon}]
    pwat = pwat.metpy.loc[{'time': time[i], 'latitude': lat, 'longitude': lon}]
    deg0l = deg0l.metpy.loc[{'time': time[i], 'latitude': lat, 'longitude': lon}]

    temp[14] = sfctemp
    uwind[14] = sfcuwind
    vwind[14] = sfcvwind
    geopot[14] = sfcgeopot
    press = np.where(press==1000, sfcpress/100, press)
    
    #sfcpress.data=92000
    
    if sfcpress.item(0) <= 95200:
                temp = np.delete(temp,13)
                qhum = np.delete(qhum,13)
                geopot = np.delete(geopot,13)
                uwind = np.delete(uwind,13)
                vwind = np.delete(vwind,13)
                press = np.delete(press,13)
                
    if sfcpress.item(0) <= 92700:
                temp = np.delete(temp,12)
                qhum = np.delete(qhum,12)
                geopot = np.delete(geopot,12)
                uwind = np.delete(uwind,12)
                vwind = np.delete(vwind,12)
                press = np.delete(press,12)
    
    k = np.size(press)-3
    
    
    press = press[::-1]
    qhum = qhum.data[::-1]*units('kg/kg')
    uwind = uwind.data[::-1]
    vwind = vwind.data[::-1]
    geopot = geopot.data[::-1]*units('meters**2/second**2')
    temp = temp-273.15
    temp = temp.data[::-1]*units.degC

    dew = mpcalc.dewpoint_from_specific_humidity(press*units.hPa, temp, qhum)
    sfcdew = sfcdew.data.item()-273.15
    dew[0] = sfcdew*units.degC
    pwat = pwat.data.item()
    pwat = pwat*units.mm
    deg0l = deg0l.data.item()
    deg0l = deg0l*units.meters
    height = mpcalc.geopotential_to_height(geopot)


    # compute convective parameters
    ws = np.sqrt(uwind**2 + vwind**2)*1.94384
    ws = list(ws)
    pressure = list(press)
    temp2 = list(temp.magnitude)
    altitude = list(height.magnitude)
    dpt= list(dew.magnitude)
    wd = mpcalc.wind_direction(uwind* units('meters/second'), vwind* units('meters/second'), convention='from')
    wd = list(wd.magnitude)
    ws = robjects.IntVector(ws)
    wd = robjects.IntVector(wd)
    dpt = robjects.IntVector(dpt)
    altitude = robjects.IntVector(altitude)
    pressure = robjects.IntVector(pressure)
    temp2 = robjects.IntVector(temp2)
    print(altitude)
    time2 = str(i+1)
    robjects.r['sounding_save'](pressure,altitude,temp2,dpt,wd,ws, max_speed=30, filename='ecmwf_sounding_stenay_%s.png' %time2,title='ECMWF | Stenay | '+ timeinit.strftime('Init: %d.%m.%Y %H:%M UTC')
              + time[i].dt.strftime(' | Valid: %d.%m.%Y %H:%M UTC').item())

Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitud

2021-05-18 00:00:00
 [1]   216   538   757   980  1443  1928  2976  4153  5496  7072  9009 10218
[13] 11718 13640 16309



Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitud

2021-05-18 00:00:00
 [1]   216   542   760   983  1444  1928  2976  4149  5490  7064  9001 10215
[13] 11711 13633 16302



Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitud

...

2021-05-18 00:00:00
 [1]   216   578   797  1021  1483  1968  3017  4195  5537  7105  9022 10233
[13] 11725 13644 16316



Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitud

2021-05-18 00:00:00
 [1]   216   587   806  1029  1491  1976  3025  4202  5545  7111  9028 10242
[13] 11732 13647 16317



Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitud

2021-05-18 00:00:00
 [1]   216   594   812  1036  1497  1982  3030  4207  5550  7113  9035 10250
[13] 11738 13649 16312



In [16]:
for i in range(48):

    data = data.metpy.parse_cf()
    data_sfc = data_sfc.metpy.parse_cf()

    time = data['z'].metpy.time

    timeinit = time[0]
    timeinit = datetime.utcfromtimestamp(timeinit.item()/1e9)-timedelta(hours=1)
    print(timeinit)

    temp = data['t']
    qhum = data['q']
    uwind = data['u']
    vwind = data['v']
    geopot = data['z']
    press = data['level']

    sfctemp = data_sfc['t2m']
    sfcdew = data_sfc['d2m']
    pwat = data_sfc['tcwv']
    deg0l = data_sfc['deg0l']
    sfcpress =  data_sfc['sp']
    sfcuwind =  data_sfc['u10']
    sfcvwind =  data_sfc['v10']
    sfcgeopot =  data_sfc['z']

    ##############################################################

    lat = 50.5
    lon = 5.9

    #i = 0 # set time step

    temp = temp.metpy.loc[{'time': time[i], 'latitude': lat, 'longitude': lon}]
    sfctemp = sfctemp.metpy.loc[{'time': time[i], 'latitude': lat, 'longitude': lon}]
    sfcdew = sfcdew.metpy.loc[{'time': time[i], 'latitude': lat, 'longitude': lon}]
    sfcpress = sfcpress.metpy.loc[{'time': time[i], 'latitude': lat, 'longitude': lon}]
    sfcuwind = sfcuwind.metpy.loc[{'time': time[i], 'latitude': lat, 'longitude': lon}]
    sfcvwind = sfcvwind.metpy.loc[{'time': time[i], 'latitude': lat, 'longitude': lon}]
    sfcgeopot = sfcgeopot.metpy.loc[{'time': time[i], 'latitude': lat, 'longitude': lon}]
    qhum = qhum.metpy.loc[{'time': time[i], 'latitude': lat, 'longitude': lon}]
    geopot = geopot.metpy.loc[{'time': time[i], 'latitude': lat, 'longitude': lon}]
    uwind = uwind.metpy.loc[{'time': time[i], 'latitude': lat, 'longitude': lon}]
    vwind = vwind.metpy.loc[{'time': time[i], 'latitude': lat, 'longitude': lon}]
    pwat = pwat.metpy.loc[{'time': time[i], 'latitude': lat, 'longitude': lon}]
    deg0l = deg0l.metpy.loc[{'time': time[i], 'latitude': lat, 'longitude': lon}]

    temp[14] = sfctemp
    uwind[14] = sfcuwind
    vwind[14] = sfcvwind
    geopot[14] = sfcgeopot
    press = np.where(press==1000, sfcpress/100, press)
    
    #sfcpress.data=92000
    
    if sfcpress.item(0) <= 95200:
                temp = np.delete(temp,13)
                qhum = np.delete(qhum,13)
                geopot = np.delete(geopot,13)
                uwind = np.delete(uwind,13)
                vwind = np.delete(vwind,13)
                press = np.delete(press,13)
                
    if sfcpress.item(0) <= 92700:
                temp = np.delete(temp,12)
                qhum = np.delete(qhum,12)
                geopot = np.delete(geopot,12)
                uwind = np.delete(uwind,12)
                vwind = np.delete(vwind,12)
                press = np.delete(press,12)
    
    k = np.size(press)-3
    
    
    press = press[::-1]
    qhum = qhum.data[::-1]*units('kg/kg')
    uwind = uwind.data[::-1]
    vwind = vwind.data[::-1]
    geopot = geopot.data[::-1]*units('meters**2/second**2')
    temp = temp-273.15
    temp = temp.data[::-1]*units.degC

    dew = mpcalc.dewpoint_from_specific_humidity(press*units.hPa, temp, qhum)
    sfcdew = sfcdew.data.item()-273.15
    dew[0] = sfcdew*units.degC
    pwat = pwat.data.item()
    pwat = pwat*units.mm
    deg0l = deg0l.data.item()
    deg0l = deg0l*units.meters
    height = mpcalc.geopotential_to_height(geopot)


    # compute convective parameters
    ws = np.sqrt(uwind**2 + vwind**2)*1.94384
    ws = list(ws)
    pressure = list(press)
    temp2 = list(temp.magnitude)
    altitude = list(height.magnitude)
    dpt= list(dew.magnitude)
    wd = mpcalc.wind_direction(uwind* units('meters/second'), vwind* units('meters/second'), convention='from')
    wd = list(wd.magnitude)
    ws = robjects.IntVector(ws)
    wd = robjects.IntVector(wd)
    dpt = robjects.IntVector(dpt)
    altitude = robjects.IntVector(altitude)
    pressure = robjects.IntVector(pressure)
    temp2 = robjects.IntVector(temp2)
    print(altitude)
    time2 = str(i+1)
    robjects.r['sounding_save'](pressure,altitude,temp2,dpt,wd,ws, max_speed=30, filename='ecmwf_sounding_spa_%s.png' %time2,title='ECMWF | Spa | '+ timeinit.strftime('Init: %d.%m.%Y %H:%M UTC')
              + time[i].dt.strftime(' | Valid: %d.%m.%Y %H:%M UTC').item())

Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitud

2021-05-18 00:00:00
 [1]   382   523   741   964  1426  1911  2960  4140  5485  7060  8989 10190
[13] 11691 13622 16298



Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitud

2021-05-18 00:00:00
 [1]   382   526   744   967  1429  1913  2960  4137  5481  7052  8980 10188
[13] 11690 13614 16288



Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitud

...

2021-05-18 00:00:00
 [1]   382   569   787  1010  1472  1957  3007  4185  5530  7097  9004 10208
[13] 11702 13628 16306



Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitud

2021-05-18 00:00:00
 [1]   382   578   796  1019  1480  1964  3013  4191  5536  7100  9007 10215
[13] 11708 13632 16308



Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitud

2021-05-18 00:00:00
 [1]   382   583   801  1024  1485  1969  3018  4196  5539  7102  9010 10221
[13] 11713 13634 16304



In [ ]:
for i in range(48):

    data = data.metpy.parse_cf()
    data_sfc = data_sfc.metpy.parse_cf()

    time = data['z'].metpy.time

    timeinit = time[0]
    timeinit = datetime.utcfromtimestamp(timeinit.item()/1e9)-timedelta(hours=1)
    print(timeinit)

    temp = data['t']
    qhum = data['q']
    uwind = data['u']
    vwind = data['v']
    geopot = data['z']
    press = data['level']

    sfctemp = data_sfc['t2m']
    sfcdew = data_sfc['d2m']
    pwat = data_sfc['tcwv']
    deg0l = data_sfc['deg0l']
    sfcpress =  data_sfc['sp']
    sfcuwind =  data_sfc['u10']
    sfcvwind =  data_sfc['v10']
    sfcgeopot =  data_sfc['z']

    ##############################################################

    lat = 50.0
    lon = 5.9

    #i = 0 # set time step

    temp = temp.metpy.loc[{'time': time[i], 'latitude': lat, 'longitude': lon}]
    sfctemp = sfctemp.metpy.loc[{'time': time[i], 'latitude': lat, 'longitude': lon}]
    sfcdew = sfcdew.metpy.loc[{'time': time[i], 'latitude': lat, 'longitude': lon}]
    sfcpress = sfcpress.metpy.loc[{'time': time[i], 'latitude': lat, 'longitude': lon}]
    sfcuwind = sfcuwind.metpy.loc[{'time': time[i], 'latitude': lat, 'longitude': lon}]
    sfcvwind = sfcvwind.metpy.loc[{'time': time[i], 'latitude': lat, 'longitude': lon}]
    sfcgeopot = sfcgeopot.metpy.loc[{'time': time[i], 'latitude': lat, 'longitude': lon}]
    qhum = qhum.metpy.loc[{'time': time[i], 'latitude': lat, 'longitude': lon}]
    geopot = geopot.metpy.loc[{'time': time[i], 'latitude': lat, 'longitude': lon}]
    uwind = uwind.metpy.loc[{'time': time[i], 'latitude': lat, 'longitude': lon}]
    vwind = vwind.metpy.loc[{'time': time[i], 'latitude': lat, 'longitude': lon}]
    pwat = pwat.metpy.loc[{'time': time[i], 'latitude': lat, 'longitude': lon}]
    deg0l = deg0l.metpy.loc[{'time': time[i], 'latitude': lat, 'longitude': lon}]

    temp[14] = sfctemp
    uwind[14] = sfcuwind
    vwind[14] = sfcvwind
    geopot[14] = sfcgeopot
    press = np.where(press==1000, sfcpress/100, press)
    
    #sfcpress.data=92000
    
    if sfcpress.item(0) <= 95200:
                temp = np.delete(temp,13)
                qhum = np.delete(qhum,13)
                geopot = np.delete(geopot,13)
                uwind = np.delete(uwind,13)
                vwind = np.delete(vwind,13)
                press = np.delete(press,13)
                
    if sfcpress.item(0) <= 92700:
                temp = np.delete(temp,12)
                qhum = np.delete(qhum,12)
                geopot = np.delete(geopot,12)
                uwind = np.delete(uwind,12)
                vwind = np.delete(vwind,12)
                press = np.delete(press,12)
    
    k = np.size(press)-3
    
    
    press = press[::-1]
    qhum = qhum.data[::-1]*units('kg/kg')
    uwind = uwind.data[::-1]
    vwind = vwind.data[::-1]
    geopot = geopot.data[::-1]*units('meters**2/second**2')
    temp = temp-273.15
    temp = temp.data[::-1]*units.degC

    dew = mpcalc.dewpoint_from_specific_humidity(press*units.hPa, temp, qhum)
    sfcdew = sfcdew.data.item()-273.15
    dew[0] = sfcdew*units.degC
    pwat = pwat.data.item()
    pwat = pwat*units.mm
    deg0l = deg0l.data.item()
    deg0l = deg0l*units.meters
    height = mpcalc.geopotential_to_height(geopot)


    # compute convective parameters
    ws = np.sqrt(uwind**2 + vwind**2)*1.94384
    ws = list(ws)
    pressure = list(press)
    temp2 = list(temp.magnitude)
    altitude = list(height.magnitude)
    dpt= list(dew.magnitude)
    wd = mpcalc.wind_direction(uwind* units('meters/second'), vwind* units('meters/second'), convention='from')
    wd = list(wd.magnitude)
    ws = robjects.IntVector(ws)
    wd = robjects.IntVector(wd)
    dpt = robjects.IntVector(dpt)
    altitude = robjects.IntVector(altitude)
    pressure = robjects.IntVector(pressure)
    temp2 = robjects.IntVector(temp2)
    print(altitude)
    time2 = str(i+1)
    robjects.r['sounding_save'](pressure,altitude,temp2,dpt,wd,ws, max_speed=30, filename='ecmwf_sounding_wiltz_%s.png' %time2,title='ECMWF | Wiltz | '+ timeinit.strftime('Init: %d.%m.%Y %H:%M UTC')
              + time[i].dt.strftime(' | Valid: %d.%m.%Y %H:%M UTC').item())

In [3]:
for i in range(48):

    data = data.metpy.parse_cf()
    data_sfc = data_sfc.metpy.parse_cf()

    time = data['z'].metpy.time

    timeinit = time[0]
    timeinit = datetime.utcfromtimestamp(timeinit.item()/1e9)-timedelta(hours=1)
    print(timeinit)

    temp = data['t']
    qhum = data['q']
    uwind = data['u']
    vwind = data['v']
    geopot = data['z']
    press = data['level']

    sfctemp = data_sfc['t2m']
    sfcdew = data_sfc['d2m']
    pwat = data_sfc['tcwv']
    deg0l = data_sfc['deg0l']
    sfcpress =  data_sfc['sp']
    sfcuwind =  data_sfc['u10']
    sfcvwind =  data_sfc['v10']
    sfcgeopot =  data_sfc['z']

    ##############################################################

    lat = 49.7
    lon = 7.3

    #i = 0 # set time step

    temp = temp.metpy.loc[{'time': time[i], 'latitude': lat, 'longitude': lon}]
    sfctemp = sfctemp.metpy.loc[{'time': time[i], 'latitude': lat, 'longitude': lon}]
    sfcdew = sfcdew.metpy.loc[{'time': time[i], 'latitude': lat, 'longitude': lon}]
    sfcpress = sfcpress.metpy.loc[{'time': time[i], 'latitude': lat, 'longitude': lon}]
    sfcuwind = sfcuwind.metpy.loc[{'time': time[i], 'latitude': lat, 'longitude': lon}]
    sfcvwind = sfcvwind.metpy.loc[{'time': time[i], 'latitude': lat, 'longitude': lon}]
    sfcgeopot = sfcgeopot.metpy.loc[{'time': time[i], 'latitude': lat, 'longitude': lon}]
    qhum = qhum.metpy.loc[{'time': time[i], 'latitude': lat, 'longitude': lon}]
    geopot = geopot.metpy.loc[{'time': time[i], 'latitude': lat, 'longitude': lon}]
    uwind = uwind.metpy.loc[{'time': time[i], 'latitude': lat, 'longitude': lon}]
    vwind = vwind.metpy.loc[{'time': time[i], 'latitude': lat, 'longitude': lon}]
    pwat = pwat.metpy.loc[{'time': time[i], 'latitude': lat, 'longitude': lon}]
    deg0l = deg0l.metpy.loc[{'time': time[i], 'latitude': lat, 'longitude': lon}]

    temp[14] = sfctemp
    uwind[14] = sfcuwind
    vwind[14] = sfcvwind
    geopot[14] = sfcgeopot
    press = np.where(press==1000, sfcpress/100, press)
    
    #sfcpress.data=92000
    
    if sfcpress.item(0) <= 95200:
                temp = np.delete(temp,13)
                qhum = np.delete(qhum,13)
                geopot = np.delete(geopot,13)
                uwind = np.delete(uwind,13)
                vwind = np.delete(vwind,13)
                press = np.delete(press,13)
                
    if sfcpress.item(0) <= 92700:
                temp = np.delete(temp,12)
                qhum = np.delete(qhum,12)
                geopot = np.delete(geopot,12)
                uwind = np.delete(uwind,12)
                vwind = np.delete(vwind,12)
                press = np.delete(press,12)
    
    k = np.size(press)-3
    
    
    press = press[::-1]
    qhum = qhum.data[::-1]*units('kg/kg')
    uwind = uwind.data[::-1]
    vwind = vwind.data[::-1]
    geopot = geopot.data[::-1]*units('meters**2/second**2')
    temp = temp-273.15
    temp = temp.data[::-1]*units.degC

    dew = mpcalc.dewpoint_from_specific_humidity(press*units.hPa, temp, qhum)
    sfcdew = sfcdew.data.item()-273.15
    dew[0] = sfcdew*units.degC
    pwat = pwat.data.item()
    pwat = pwat*units.mm
    deg0l = deg0l.data.item()
    deg0l = deg0l*units.meters
    height = mpcalc.geopotential_to_height(geopot)


    # compute convective parameters
    ws = np.sqrt(uwind**2 + vwind**2)*1.94384
    ws = list(ws)
    pressure = list(press)
    temp2 = list(temp.magnitude)
    altitude = list(height.magnitude)
    dpt= list(dew.magnitude)
    wd = mpcalc.wind_direction(uwind* units('meters/second'), vwind* units('meters/second'), convention='from')
    wd = list(wd.magnitude)
    ws = robjects.IntVector(ws)
    wd = robjects.IntVector(wd)
    dpt = robjects.IntVector(dpt)
    altitude = robjects.IntVector(altitude)
    pressure = robjects.IntVector(pressure)
    temp2 = robjects.IntVector(temp2)
    print(altitude)
    time2 = str(i+1)
    robjects.r['sounding_save'](pressure,altitude,temp2,dpt,wd,ws, max_speed=30, filename='ecmwf_sounding_idarob_%s.png' %time2,title='ECMWF | Idar-Oberstein | '+ timeinit.strftime('Init: %d.%m.%Y %H:%M UTC')
              + time[i].dt.strftime(' | Valid: %d.%m.%Y %H:%M UTC').item())

Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitud

2022-06-09 00:00:00
 [1]   449   528   751   978  1449  1942  3011  4215  5596  7210  9189 10422
[13] 11920 13826 16482



Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitud

2022-06-09 00:00:00
 [1]   449   528   750   977  1448  1941  3011  4214  5593  7206  9187 10425
[13] 11923 13828 16480



Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitud

...

2022-06-09 00:00:00
 [1]   449   626   852  1084  1561  2060  3152  4390  5816  7489  9524 10749
[13] 12197 14013 16582



Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitud

2022-06-09 00:00:00
 [1]   449   627   853  1084  1561  2060  3152  4389  5815  7487  9521 10747
[13] 12194 14009 16579



Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitude/longitude coordinates, assuming latitude_longitude for projection grid_mapping variable
Found valid latitud

2022-06-09 00:00:00
 [1]   449   627   853  1084  1561  2060  3151  4388  5812  7485  9517 10743
[13] 12189 14005 16576

